In [1]:
%load_ext autoreload
%autoreload 2

import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

workding dir: /Users/inflaton/code/engd/papers/maritime/global-incidents
loading env vars from: /Users/inflaton/code/engd/papers/maritime/global-incidents/.env


True

In [2]:
import nltk
from nltk.tokenize import sent_tokenize
from nltk.tokenize import word_tokenize

import gensim
from gensim import corpora
from gensim import similarities
from gensim import models
from gensim.models import CoherenceModel

# from wordcloud import WordCloud, ImageColorGenerator
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import re
import os
import datetime

import warnings
warnings.filterwarnings('ignore')

from pprint import pprint
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis

# Import Data

In [3]:
df = pd.read_parquet('data/processed_data2.parquet')

In [4]:
df.head()

id                                           Headline  \
0   1  Grasberg Mine- Grasberg mine workers extend st...   
1   3  Shanghai port congestion impacts terminals in ...   
2   5  UPDATE - Indonesia: Police confirm two explosi...   
3   6  UPDATE - Indonesia: Severe winds damage infras...   
4  14  2 miles E of Chesterfield - A tornado has touc...   

                                             Details  Severity  \
0  Media sources indicate that workers at the Gra...  Moderate   
1  The persisting port congestion at Shanghai’s Y...     Minor   
2  According to local police in Jakarta, two expl...   Extreme   
3  Severe winds have downed billboards and trees ...  Moderate   
4  Government sources are reporting a tornado has...     Minor   

                                            Category         Region  \
0                                Mine Workers Strike      Indonesia   
1                                    Port Congestion          China   
2                         Bombing, Police Operations      Indonesia   
3  Roadway Closure / Disruption, Flooding, Severe...      Indonesia   
4                                            Tornado  United States   

        Datetime    Year       lat        lon  ...  if_labeled Month  Week  \
0  28/5/17 17:08  2017.0  -4.05608  137.11302  ...       False   5.0  21.0   
1   27/4/17 9:16  2017.0  29.52000  121.33190  ...       False   4.0  17.0   
2  24/5/17 16:20  2017.0       NaN        NaN  ...        True   5.0  21.0   
3   19/4/17 9:10  2017.0  -6.91264  107.65700  ...        True   4.0  16.0   
4  17/9/18 19:55  2018.0  37.51000  -77.61000  ...        True   9.0  38.0   

                                    Headline_Details  \
0  Grasberg Mine- Grasberg mine workers extend st...   
1  Shanghai port congestion impacts terminals in ...   
2  UPDATE - Indonesia: Police confirm two explosi...   
3  UPDATE - Indonesia: Severe winds damage infras...   
4  2 miles E of Chesterfield - A tornado has touc...   

                                                 url  \
0  https://news.google.com/rss/articles/CBMiZ2h0d...   
1  https://news.google.com/rss/articles/CBMiVWh0d...   
2  https://news.google.com/rss/articles/CBMiZWh0d...   
3  https://news.google.com/rss/articles/CBMiSWh0d...   
4  https://news.google.com/rss/articles/CBMigAFod...   

                                               title  \
0  Freeport Indonesia mine workers extend strike ...   
1  Typhoon Muifa to shut China ports for second t...   
2  Jakarta Police Receive 2 More Reports on Coldp...   
3  Indonesia hit by some of strongest winds recorded   
4  UPDATE: Number of homes without power down to ...   

                                             content  \
0  Trucks are seen on a road in the Grasberg copp...   
1  By Sam Whelan 13/09/2022\n\nAnother typhoon ha...   
2  TEMPO.CO, Jakarta - South Jakarta Metro Police...   
3  A man stands near damaged houses following a t...   
4  More than 90,000 homes and businesses across t...   

                                     cleaned_content  \
0  [truck, be, see, on, road, in, grasberg, coppe...   
1  [by, sam, whelan, typhoon, have, prompt, port,...   
2  [jakarta, south, jakarta, metro, police, recei...   
3  [man, stand, near, damage, house, follow, torn...   
4  [more, than, home, business, across, richmond,...   

                                      binary_content word_count  
0  [adkerson_jakarta_try, agreement_freeport_indo...         53  
1  [additional_ripple_effect, avoid_path_typhoon,...         44  
2  [actress_accord, available_day_concert, click_...         24  
3  [bbc_indonesia, climatologist_government_resea...         28  
4  [advise_seek_alternate, affect_richmond, alter...        134  

[5 rows x 23 columns]

In [5]:
df.shape

(3681, 23)

# Vectorisation

NLP vectorization refers to the process of converting text data into numerical vectors that machine learning algorithms can understand and process. 

Bag-of-Words (BoW) is used here that represents text as a collection of unique words along with their frequencies. Each word is assigned an index, and the vector contains the count of each word present in the document.

In [6]:
df_copy = df.copy()

In [7]:
# choose only the extreme and severe cases for modelling
cleaned = df_copy[df_copy['Severity'].isin(['Minor'])]
cleaned.reset_index(drop=True, inplace=True)

In [8]:
cleaned.shape

(1620, 23)

In [9]:
headline = cleaned.cleaned_content

In [10]:
headline[5]

array(['man', 'be', 'seriously', 'injure', 'after', 'boat', 'catch',
       'fire', 'in', 'sydney', 'marina', 'today', 'emergency', 'service',
       'be', 'call', 'birkenhead', 'point', 'marina', 'in', 'drummoyne',
       'shortly', 'after', 'follow', 'report', 'of', 'explosion', 'on',
       'boat', 'careflight', 's', 'rapid', 'response', 'helicopter', 'be',
       'task', 'at', 'crew', 'include', 'doctor', 'intensive', 'care',
       'paramedic', 'fly', 'drummoyne', 'land', 'in', 'nearby', 'brett',
       'park', 'just', 'minute', 'late', 'careflight', 'boat', 'catch',
       'fire', 'near', 'birkenhead', 'point', 'shopping', 'outlet',
       'simon', 'r', 'supply', 'reader', 'image', 'of', 'boat', 'on',
       'fire', 'at', 'marina', 'in', 'drummoyne', 'simon', 'r', 'supply',
       'three', 'nsw', 'ambulance', 'crew', 'careflight', 'chopper',
       'attend', 'scene', 'find', 'man', 'suffer', 'serious', 'burn',
       'legs', 'arm', 'shoulder', 'man', 'suffer', 'burn', 'percent',


In [11]:
# vectorise the words
doc_dict = gensim.corpora.Dictionary(headline)
docs_vecs = [doc_dict.doc2bow(doc) for doc in headline]

In [12]:
print('Number of unique tokens: %d' % len(doc_dict)) 
print('Number of articles: %d' % len(docs_vecs)) 

Number of unique tokens: 35192
Number of articles: 1620


In [13]:
# Calculate word frequencies
word_frequencies = {doc_dict[word_id]: freq for word_id, freq in doc_dict.cfs.items()}
sorted_words = sorted(word_frequencies.items(), key=lambda x: x[1], reverse=True)

pprint(sorted_words[:100])

[('be', 58147),
 ('of', 53324),
 ('in', 42710),
 ('for', 19846),
 ('on', 18899),
 ('have', 18769),
 ('with', 13029),
 ('as', 12079),
 ('port', 11548),
 ('from', 11033),
 ('at', 10589),
 ('by', 10527),
 ('s', 8527),
 ('will', 8465),
 ('that', 7825),
 ('say', 7752),
 ('not', 5664),
 ('china', 5654),
 ('day', 5304),
 ('more', 5266),
 ('new', 5198),
 ('service', 5001),
 ('also', 4707),
 ('ship', 4693),
 ('time', 4651),
 ('than', 3673),
 ('year', 3669),
 ('trade', 3518),
 ('can', 3504),
 ('state', 3378),
 ('between', 3226),
 ('include', 3220),
 ('over', 3173),
 ('supply', 3094),
 ('do', 3083),
 ('vessel', 3079),
 ('report', 2988),
 ('country', 2979),
 ('after', 2962),
 ('area', 2913),
 ('cargo', 2908),
 ('one', 2905),
 ('people', 2868),
 ('other', 2866),
 ('increase', 2852),
 ('continue', 2787),
 ('market', 2766),
 ('container', 2765),
 ('strike', 2713),
 ('chain', 2708),
 ('expect', 2656),
 ('work', 2624),
 ('while', 2590),
 ('high', 2579),
 ('about', 2514),
 ('http', 2489),
 ('into', 2470

# LDA Modelling

## Benchmark Model

In [14]:
# Build LDA benchmark model
lda_model = gensim.models.LdaMulticore(corpus=docs_vecs,
                                       id2word=doc_dict,
                                       num_topics=4, 
                                       random_state=42,
                                       chunksize=100,
                                       passes=10,
                                       per_word_topics=True)

In [15]:
from pprint import pprint

# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[docs_vecs]

[(0,
  '0.042*"of" + 0.030*"in" + 0.026*"be" + 0.012*"china" + 0.012*"on" + '
  '0.011*"s" + 0.011*"for" + 0.011*"have" + 0.010*"that" + 0.009*"as"'),
 (1,
  '0.028*"be" + 0.028*"of" + 0.018*"in" + 0.011*"de" + 0.009*"y" + 0.009*"for" '
  '+ 0.008*"by" + 0.007*"http" + 0.007*"on" + 0.007*"have"'),
 (2,
  '0.041*"be" + 0.033*"of" + 0.028*"in" + 0.015*"on" + 0.013*"have" + '
  '0.013*"for" + 0.009*"at" + 0.009*"say" + 0.009*"as" + 0.008*"with"'),
 (3,
  '0.039*"be" + 0.029*"of" + 0.026*"in" + 0.018*"port" + 0.013*"for" + '
  '0.011*"have" + 0.009*"on" + 0.009*"with" + 0.009*"day" + 0.008*"from"')]


In [16]:
# Compute Benchmark Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=headline, dictionary=doc_dict, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score LDAModel: ', coherence_lda)


Coherence Score LDAModel:  0.2757800922361482


In [17]:
# Compute Benchmark Perplexity
perplex= lda_model.log_perplexity(docs_vecs, total_docs=None) #For LDAModel
  # a measure of how good the model is. lower the better.

print('\nPerplexity for LDAModel: ', perplex)


Perplexity for LDAModel:  -7.407722316633226


In [18]:
from pprint import pprint
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis

# feed the LDA model into the pyLDAvis instance
pyLDAvis.enable_notebook()
visual= gensimvis.prepare(lda_model, docs_vecs, doc_dict)

# Save the output to the html file
pyLDAvis.save_html(visual, "data/topic_viz_benchmark_minor.html")

/Users/inflaton/anaconda3/envs/maritime/lib/python3.12/site-packages/joblib/externals/loky/backend/fork_exec.py:38: DeprecationWarning: This process (pid=39505) is multi-threaded, use of fork() may lead to deadlocks in the child.
  pid = os.fork()
/Users/inflaton/anaconda3/envs/maritime/lib/python3.12/site-packages/joblib/externals/loky/backend/fork_exec.py:38: DeprecationWarning: This process (pid=39505) is multi-threaded, use of fork() may lead to deadlocks in the child.
  pid = os.fork()
/Users/inflaton/anaconda3/envs/maritime/lib/python3.12/site-packages/joblib/externals/loky/backend/fork_exec.py:38: DeprecationWarning: This process (pid=39505) is multi-threaded, use of fork() may lead to deadlocks in the child.
  pid = os.fork()
/Users/inflaton/anaconda3/envs/maritime/lib/python3.12/site-packages/joblib/externals/loky/backend/fork_exec.py:38: DeprecationWarning: This process (pid=39505) is multi-threaded, use of fork() may lead to deadlocks in the child.
  pid = os.fork()
/Users/i

# Hyper-Perameter Tuning and Evaluation

Run the cells below only for re-modelling with new datasets, the whole tuning and evaluation process may take hours to run.

In [19]:
# hyper-perameter tuning (alpha and beta)
def compute_coherence_values(corpus, dictionary, k, a, b):
    
    lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                           id2word=dictionary,
                                           num_topics=k, 
                                           random_state=42,
                                           chunksize=100,
                                           passes=10,
                                           alpha=a,
                                           eta=b)
    
    coherence_model_lda = CoherenceModel(model=lda_model, texts=headline, dictionary=doc_dict, coherence='c_v')
    coherence = coherence_model_lda.get_coherence()
    perplex = lda_model.log_perplexity(docs_vecs, total_docs=None) 
    
    return coherence, perplex

In [20]:
# setup
import numpy as np

from gensim.models import CoherenceModel

model_list = []
coherence_values = []
perplexity_values = []
model_topics = []
alpha_result = []
beta_result = []

# topic ranges
num_topics = range(4, 13)

# Alpha parameter
alpha = list(np.arange(0.31, 1, 0.3))
alpha.append('symmetric')
alpha.append('asymmetric')

# Beta parameter
beta = list(np.arange(0.31, 1, 0.3))
beta.append('symmetric')

Rational behind the alpha and eta: https://stats.stackexchange.com/questions/37405/natural-interpretation-for-lda-hyperparameters

In [21]:
print("Topic range: ",num_topics)
print("Alpha: ",alpha)
print("Beta: ", beta)

Topic range:  range(4, 13)
Alpha:  [0.31, 0.61, 0.9099999999999999, 'symmetric', 'asymmetric']
Beta:  [0.31, 0.61, 0.9099999999999999, 'symmetric']


In [23]:
%%time

import datetime
import numpy as np
from gensim.models import CoherenceModel

print(datetime.datetime.now())

for a in alpha:
    for b in beta:
        for num in num_topics:
            cv, pv = compute_coherence_values(corpus=docs_vecs, dictionary=doc_dict,k=num, a=a, b=b) 

            model_topics.append(num)    
            coherence_values.append(cv)  
            perplexity_values.append(pv)
            alpha_result.append(a)
            beta_result.append(b)
            print("#Topics: " + str(num) + ", CV Score: " + str(coherence_values[-1]) + ", PV Score: " + str(perplexity_values[-1]) + ", Alpha: " + str(alpha_result[-1]) + ", Beta: " + str(beta_result[-1]))
    
print(datetime.datetime.now())

2024-06-30 11:52:46.026823
#Topics: 4, CV Score: 0.26143167370104753, PV Score: -7.394241913115894, Alpha: 0.31, Beta: 0.31
#Topics: 5, CV Score: 0.29008917581081944, PV Score: -7.35821379289522, Alpha: 0.31, Beta: 0.31
#Topics: 6, CV Score: 0.3075550457683199, PV Score: -7.348746753666222, Alpha: 0.31, Beta: 0.31
#Topics: 7, CV Score: 0.27068500671158163, PV Score: -7.332448354134598, Alpha: 0.31, Beta: 0.31
#Topics: 8, CV Score: 0.2949752069963174, PV Score: -7.355618761173559, Alpha: 0.31, Beta: 0.31
#Topics: 9, CV Score: 0.2883770109840239, PV Score: -7.345756037675643, Alpha: 0.31, Beta: 0.31
#Topics: 10, CV Score: 0.30169838729877146, PV Score: -7.334658077515814, Alpha: 0.31, Beta: 0.31
#Topics: 11, CV Score: 0.28399502160009293, PV Score: -7.337863652882048, Alpha: 0.31, Beta: 0.31
#Topics: 12, CV Score: 0.3098908373731854, PV Score: -7.317278302545894, Alpha: 0.31, Beta: 0.31
#Topics: 4, CV Score: 0.26324058496974073, PV Score: -7.421960949456933, Alpha: 0.31, Beta: 0.61
#Topi

KeyboardInterrupt: 

The table below reveals the top 20 fine tuned models with best combinations of coherence score and perplexity score. It was sorted by the coherence score in descending order as a higher coherence score indicates a better model, and sorted the perplexity score in ascending order as a lower perplexity score indicates a better model. While coherence score evaluates the quality of the topics, the perplexity score evaluates the overall performance of the model in predicting new documents. Usually, the coherence score is a better metric to use if the goal is to obtain topics that are semantically coherent and interpretable. Perplexity score, on the other hand, is a better metric to use if the goal is to build a model that generalises well to new data, in other words, how confident the model is in predicting the new data (Sánchez-Aguayo, et al., 2022). Ultimately, we aim to get a balance between the perplexity value and coherence score when determining our final model.

In [ ]:
# Find the top 20 combinations based on Coherence Score and Perplexity Score
result = pd.DataFrame(
    {'Topics': model_topics,
     'Coherence Score': coherence_values,
     'Perplexity Score': perplexity_values,
     'Alpha': alpha_result,
     'Beta': beta_result
    })
result.sort_values(by=['Coherence Score', 'Perplexity Score'], ascending=[False, True]).head(20)

In [ ]:
result.to_csv('data/lda_fine_tuning_result_minor.csv')

In [ ]:
# Show graph Topics vs Coherence Score
result.groupby('Alpha').plot(x='Topics', y='Coherence Score', legend = True)

In [ ]:
# Show graph Topics vs Perplexity Score

plt.plot(model_topics, coherence_values)
plt.xlabel("Num Topics")
plt.ylabel("Coherence Score")
plt.legend(("Coherence Score"), loc='best')
plt.show()

In [ ]:
# Show graph Topics vs Perplexity Score

plt.plot(model_topics, perplexity_values)
plt.xlabel("Num Topics")
plt.ylabel("Perplexity score")
plt.legend(("perplexity_values"), loc='best')
plt.show()

## Final Model

refer to the script topic_modelling_severe for detailed explanation

In [ ]:
# realised that there may be some overlaps for 8 topics, thus 4-6 topics are optimal
k = 2
# a = 'asymmetric'
a = 0.31
# b = 0.31
b = 'symmetric'


final_model = gensim.models.LdaMulticore(corpus=docs_vecs,
                                           id2word=doc_dict,
                                           num_topics=k, 
                                           random_state=42,
                                           chunksize=100,
                                           passes=10,
                                           alpha=a,
                                           eta=b)

In [ ]:
compute_coherence_values(corpus=docs_vecs, dictionary=doc_dict,k=k, a=a, b=b) 

In [ ]:
# Set up the environment to display the graphical outputs
# feed the LDA model into the pyLDAvis instance
pyLDAvis.enable_notebook()
visual= gensimvis.prepare(final_model, docs_vecs, doc_dict)

# Save the output to the html file
pyLDAvis.save_html(visual, "data/topic_viz2_minor_training.html")

In [ ]:
final_model.print_topics(num_words=30)

In [ ]:
break

In [ ]:
# Map the topic ID with appropriate topic names, this part should be updated accordinly whenever the model is updated
topic_mapping = {0: "finance", 1: "tech", 2: "education", 3: "sports", 4: "leisure"}

In [ ]:
# Get the topics and their top keywords into a dataframe
topics = final_model.show_topics(num_words=30) 

topic_keywords = pd.DataFrame()
for topic_id, topic in topics:
    topic_keywords.at[topic_id, 'Topic Keywords'] = topic

topic_keywords['Topic ID'] = topic_keywords.index
topic_keywords['Topic Name'] = topic_mapping 
topic_keywords

# Save the final model 

In [ ]:
#Save a model to disk, or reload a pre-trained model
# naming convention: final_model_topic_alpha_eta
final_model.save("models/final_model_5_asym_91")

# Find dominant topic(s) for each news article

Attach the dominant topics back to the news dataset for classifying purpose.

Made use of gensim lda's own function: https://radimrehurek.com/gensim/models/ldamodel.html

In [ ]:
import warnings
warnings.filterwarnings('ignore')

def format_topics_sentences(ldamodel, corpus, data):
    # Preallocate memory for the DataFrame
    num_docs = len(corpus)
    sent_topics = {'Dominant_Topic': [0] * num_docs, 'Perc_Contribution': [0.0] * num_docs, 'Topic_Distribution': [()] * num_docs}
    
    # Get main topic in each document
    for i, row in enumerate(ldamodel[corpus]):
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        if row:
            # Get the Dominant topic, Perc Contribution and Keywords for each document
            dominant_topic, perc_contribution = row[0]
            topic_distribution = row
            sent_topics['Dominant_Topic'][i] = int(dominant_topic)
            sent_topics['Perc_Contribution'][i] = round(perc_contribution, 4)
            sent_topics['Topic_Distribution'][i] = topic_distribution

    # Create the DataFrame
    sent_topics_df = pd.DataFrame(sent_topics)
    sent_topics_df['Text'] = data

    return sent_topics_df

In [ ]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=final_model, corpus=docs_vecs, data=cleaned.Headline_Details)

In [ ]:
# Format
df_dominant_topic = df_topic_sents_keywords.reset_index()
df_dominant_topic.columns = ['Document_No', 'Dominant_Topic', 'Topic_Perc_Contrib', 'Topic_Distribution', 'Text']

# Show
df_dominant_topic.head(10)

# Result Analysis

In [ ]:
df_dominant_topic["Dominant_Topic"].value_counts()

In [ ]:
import matplotlib.pyplot as plt

# Get value counts of each topic
topic_counts = df_dominant_topic["Dominant_Topic"].value_counts()

# Create a bar plot
plt.figure(figsize=(8, 6))
topic_counts.plot(kind="bar", color="skyblue")

# Add labels to the bars
for i, count in enumerate(topic_counts):
    plt.text(i, count, str(count), ha="center", va="bottom")

# Add labels and title
plt.xlabel("Topics")
plt.ylabel("Number of News")
plt.title("Topic Distribution")

# Show the plot
plt.xticks(rotation=45)  # Rotate x-axis labels for better readability
plt.tight_layout()
plt.show()


In [ ]:
df_dominant_topic.sort_values(by='Topic_Perc_Contrib', ascending=True).head(20)

In [ ]:
# Sample 100 rows, can change the random_state for different samples
sampled_data = df_dominant_topic.sample(n=100, random_state=42)  
sampled_df = pd.DataFrame(sampled_data).reset_index()
sampled_df.to_csv('data/sample_minor.csv')